# Deliverable 3. Create a Travel Itinerary Map

----

1. Create a folder called `Vacation_Itinerary` to store all the files for this deliverable.

2. Download the `Vacation_Itinerary_starter_code.ipynb` file into your `Vacation_Itinerary` folder and rename it `Vacation_Itinerary.ipynb`.

3. Make sure the initial dependencies and the Geoapify API key are imported.

4. From your `Vacation_Search` folder from Deliverable 2, import the `WeatherPy_vacation.csv` file as a DataFrame named `vacation_df`.

5. Use GeoViews to create a map that shows all the cities in the `vacation_df` DataFrame. Configure the map as follows:

    * The point's size should be the maximum temperature for the city

    * The point's color should be the city's name

    * Use the `hover_cols` parameter to the the "Hotel Name", "Country", and "Current Description" columns to each point as additional information.

6. From the map, *choose four cities* that a customer might want to visit. They should be close together and in the same country. Use the `loc` method to create separate DataFrames for each city on the travel route.

    > **Hint:** You will start and end the route in the same city, so the `vacation_start` and `vacation_end` DataFrames will be in the same city.

7. Use the Pandas `concat` function to merge the DataFrame from each city in the itinerary to create a new DataFrame named `itinerary_df` to store the itinerary details.

8. Use the Pandas `copy` function to create a new DataFrame named `waypoints_df` to store the longitude and latitude for each city in `itinerary_df`.

    > **Hint:** You'll use this DataFrame to create a map using GeoViews, so recall that the first column should be the longitude, and the second the latitude.

9. Use GeoViews to create a map that shows the four cities in the itinerary.

10. Next, you'll use the Geoapify Routing API to find a route between the cities in the itinerary. Review the code that sets the initial parameters and fetches the coordinates from each city to define the `waypoints` parameter by using a `for` loop.

    > **Hint:** You can note that the `mode` parameter is set to `drive`, you can play around with other modes as it's shown in [the "Travel modes" table](https://apidocs.geoapify.com/docs/routing/#api) in the Geoapify Routing API documentation.

11. Use the Geoapify Routing API to retrieve the route's directions for your itinerary.

12. From the JSON response, store the route's legs coordinates in a variable called `legs`.

13. Loop through the route legs coordinates to fetch the latitude and longitude for each step. Store the latitude and longitude values into two Python lists named `longitude` and `latitude`.

14. Use the `longitude` and `latitude` Python lists to create a new DataFrame named `route_df`.

15. Use the GeoViews `Path` function to configure a line plot by using `route_df`. Set a custom color and width for the line that may contrast with the map.

16. Use the asterisk operator to display a composed plot that shows the itinerary's route over the map containing the cities. 

17. Save your map to the `Vacation_Itinerary` folder as `WeatherPy_travel_map.png`.

---

## Make sure the initial dependencies and the Geoapify API key are imported

In [1]:
# Dependencies and Setup
import geoviews as gv
import hvplot.pandas
import pandas as pd
import requests

# Turn off warning messages
import warnings
warnings.filterwarnings("ignore")

# Import API key
from config import geoapify_key

## From your `Vacation_Search` folder from Deliverable 2, import the `WeatherPy_vacation.csv` file as a DataFrame named `vacation_df`

In [2]:
# Read the WeatherPy_vacation.csv into a DataFrame
vacation_df = pd.read_csv("../Vacation_Search/WeatherPy_vacation.csv")

# Display sample data
vacation_df.head(5)

City_ID            City Country  Max Temp Current Description      Lat  \
0        1            Hilo      US     78.53       moderate rain  19.7297   
1        3           Tabou      CI     78.24     overcast clouds   4.4230   
2        6    Puerto Ayora      EC     70.56    scattered clouds  -0.7393   
3        7         Rikitea      PF     75.85           clear sky -23.1203   
4       16  Saint-Philippe      RE     72.99          light rain -21.3585   

        Lng                            Hotel Name  
0 -155.0900                     Dolphin Bay Hotel  
1   -7.3528                       hôtel le rochet  
2  -90.3518  Hostal La Mirada De Solitario George  
3 -134.9692                  Chez Bianca & Benoit  
4   55.7679                              Le Baril

## Use GeoViews to create a map that shows all the cities in the `vacation_df` DataFrame. Configure the map as follows:

* The point's size should be the maximum temperature for the city

* The point's color should be the city's name

* Use the `hover_cols` parameter to the the "Hotel Name", "Country", and "Current Description" columns to each point as additional information.

In [3]:
# Configure the map plot
map_plot = vacation_df.hvplot.points(
    "Lng",
    "Lat",
    geo = True,
    tiles = "OSM",
    frame_width = 600,
    frame_height = 400,
    size = "Max Temp",
    scale = 0.8,
    color = "City",
    hover_cols = ["Hotel Name", "Country","Current Description"]
)

# Display the map
map_plot

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City,Max Temp,Hotel Name,Country,Current Description)

## From the map, *choose four cities* that a customer might want to visit. They should be close together and in the same country. Use the `loc` method to create separate DataFrames for each city on the travel route.

In [4]:
# Create DataFrames for each city by filtering the 'vacation_df' using the loc method
vacation_start = vacation_df.loc[vacation_df["City"]=="Cabo San Lucas"]
vacation_end = vacation_df.loc[vacation_df["City"]=="Acapulco"]
vacation_stop1 = vacation_df.loc[vacation_df["City"]=="Tomatlan"]
vacation_stop2 = vacation_df.loc[vacation_df["City"]=="Pochutla"]

## Use the Pandas `concat` function to merge the DataFrame from each city in the itinerary to create a new DataFrame named `itinerary_df` to store the itinerary details

In [5]:
# Use the Pandas concat function to create a new DataFrame to store the itinerary details.
itinerary_df = pd.concat([vacation_start,vacation_end,vacation_stop1,vacation_stop2])
# Display sample data
itinerary_df

City_ID            City Country  Max Temp Current Description      Lat  \
80      328  Cabo San Lucas      MX     75.51     overcast clouds  22.8909   
59      254        Acapulco      MX     76.96     overcast clouds  16.8634   
65      269        Tomatlan      MX     71.82           clear sky  19.9333   
60      256        Pochutla      MX     77.83    scattered clouds  15.7432   

         Lng                     Hotel Name  
80 -109.9124                  Comfort Rooms  
59  -99.8901                Hotel del Valle  
65 -105.2500  Hotel Hacienda Vieja Tomatlan  
60  -96.4661                 Hotel El Patio

## Use the Pandas `copy` function to create a new DataFrame named `waypoints_df` to store the longitude and latitude for each city in `itinerary_df`

In [6]:
# Create a Pandas DataFrame to store the latitude and longitude for each city in the itineray
waypoints_df = itinerary_df[['Lat','Lng','City']].copy()

# Display sample data
waypoints_df

Lat       Lng            City
80  22.8909 -109.9124  Cabo San Lucas
59  16.8634  -99.8901        Acapulco
65  19.9333 -105.2500        Tomatlan
60  15.7432  -96.4661        Pochutla

## Use GeoViews to create map that shows the four cities in the itinerary

In [32]:
# Configure the map plot by using the itineraty_df
waypoints_map = itinerary_df.hvplot.points(
    "Lng",
    "Lat",
    geo = True,
    tiles = "EsriStreet",
    frame_width = 600,
    frame_height = 400,
    scale = 0.8,
    size=300,
    color = "City",
    hover_cols = ["City"]
)


In [33]:
# Display the route_map
waypoints_map

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City)

## Next, you'll use the Geoapify Routing API to find a route between the cities in the itinerary. Review the code that sets the initial parameters and fetches the coordinates from each city to define the `waypoints` parameter by using a `for` loop

In [9]:
# Set parameters to trace the route
radius = 5000
params = {
    "mode":"drive",
    "apiKey": geoapify_key,
}

In [10]:
# Set an empty waypoints String variable
waypoints = ""

# Iterate through the route_df DataFrame to define the waypoints
for index, row in waypoints_df.iterrows():
    waypoints = waypoints + str(row["Lat"]) + "," + str(row["Lng"]) + "|"

# Delete the last character from the string
waypoints = waypoints[:-1]

# Add the waypoints to the params dictionary
params["waypoints"] = waypoints

# Display the params dictionary
params

{'mode': 'drive',
 'apiKey': 'a32839b1785343c58c8d995adc4a7019',
 'waypoints': '22.8909,-109.9124|16.8634,-99.8901|19.9333,-105.25|15.7432,-96.4661'}

## Use the Geoapify Routing API to retrieve the route's directions for your itinerary

In [11]:
# Set up the base URL for the Geoapify Places API.
base_url = "https://api.geoapify.com/v1/routing"

# Make request and retrieve the JSON data by using the params dictionaty
route_response = requests.get(base_url, params=params).json()

# Convert the API response to JSON format
route_response

{'features': [{'type': 'Feature',
   'properties': {'mode': 'drive',
    'waypoints': [{'location': [-109.9124, 22.8909], 'original_index': 0},
     {'location': [-99.8901, 16.8634], 'original_index': 1},
     {'location': [-105.25, 19.9333], 'original_index': 2},
     {'location': [-96.4661, 15.7432], 'original_index': 3}],
    'units': 'metric',
    'distance': 6472886,
    'distance_units': 'meters',
    'time': 262422.523,
    'legs': [{'distance': 4300913,
      'time': 167668.296,
      'steps': [{'from_index': 0,
        'to_index': 4,
        'distance': 327,
        'time': 28.491,
        'instruction': {'text': 'Drive southeast on Avenida Leona Vicario.'}},
       {'from_index': 4,
        'to_index': 30,
        'distance': 1074,
        'time': 76.21,
        'instruction': {'text': 'Turn left onto Boulevard Lazaro Cardenas.'}},
       {'from_index': 30,
        'to_index': 57,
        'distance': 1155,
        'time': 113.967,
        'instruction': {'text': 'Turn left on

## From the JSON response, store the route's legs coordinates in a variable called `legs`

In [12]:
# Fetch the route's legs coordinates from the JSON reponse
legs = route_response['features'][0]['geometry']['coordinates']
legs

[[[-109.912519, 22.890833],
  [-109.912093, 22.890194],
  [-109.911563, 22.889428],
  [-109.911134, 22.888784],
  [-109.910801, 22.888351],
  [-109.910768, 22.888334],
  [-109.910726, 22.888322],
  [-109.910695, 22.888319],
  [-109.910669, 22.888323],
  [-109.910641, 22.888332],
  [-109.910619, 22.888345],
  [-109.910603, 22.888359],
  [-109.910581, 22.888382],
  [-109.910484, 22.888532],
  [-109.909568, 22.889925],
  [-109.909038, 22.890713],
  [-109.908951, 22.890836],
  [-109.908665, 22.891261],
  [-109.908359, 22.891723],
  [-109.908194, 22.891966],
  [-109.907663, 22.892819],
  [-109.907512, 22.893053],
  [-109.906922, 22.894006],
  [-109.906557, 22.894565],
  [-109.90616, 22.895151],
  [-109.906009, 22.895358],
  [-109.905813, 22.895606],
  [-109.905597, 22.895849],
  [-109.905396, 22.896044],
  [-109.905168, 22.89624],
  [-109.905079, 22.896294],
  [-109.905164, 22.896399],
  [-109.905225, 22.896483],
  [-109.905366, 22.896689],
  [-109.90566, 22.897079],
  [-109.906029, 22.8976

## Loop through the route legs coordinates to fetch the latitude and longitude for each step. Store the latitude and longitude value into two Python lists names `longitude` and `latitude`

In [13]:
# Create and empty list to store the longitude of each step
lons = []

# Create and empty list to store the latitude of step
lats = []

# Loop through the legs coordinates to fetch the latitude and longitude for each step
for coord in legs:
    for x in coord:  
        lats.append(x[0])
        lons.append(x[1])

lats

[-109.912519,
 -109.912093,
 -109.911563,
 -109.911134,
 -109.910801,
 -109.910768,
 -109.910726,
 -109.910695,
 -109.910669,
 -109.910641,
 -109.910619,
 -109.910603,
 -109.910581,
 -109.910484,
 -109.909568,
 -109.909038,
 -109.908951,
 -109.908665,
 -109.908359,
 -109.908194,
 -109.907663,
 -109.907512,
 -109.906922,
 -109.906557,
 -109.90616,
 -109.906009,
 -109.905813,
 -109.905597,
 -109.905396,
 -109.905168,
 -109.905079,
 -109.905164,
 -109.905225,
 -109.905366,
 -109.90566,
 -109.906029,
 -109.906159,
 -109.906211,
 -109.906623,
 -109.906826,
 -109.907046,
 -109.907341,
 -109.907516,
 -109.90762,
 -109.907742,
 -109.907927,
 -109.908228,
 -109.908395,
 -109.908497,
 -109.908621,
 -109.908808,
 -109.908995,
 -109.909152,
 -109.909411,
 -109.910786,
 -109.912747,
 -109.913666,
 -109.914306,
 -109.915283,
 -109.916209,
 -109.917228,
 -109.917935,
 -109.918106,
 -109.918229,
 -109.918362,
 -109.918454,
 -109.918539,
 -109.918633,
 -109.918731,
 -109.918847,
 -109.918965,
 -109.919

## Use the `longitude` and `latitude` Python lists to create a new DataFrame named `route_df`

In [14]:
# Create an empty DataFrame to store the steps' coordinates
route_df = pd.DataFrame()

# Add the steps' longitude and latitude from each step as columns to the DataFrame
route_df["Latitude"] = lats
route_df["Longitude"] = lons

# Display sample data
route_df.head(10)

Latitude  Longitude
0 -109.912519  22.890833
1 -109.912093  22.890194
2 -109.911563  22.889428
3 -109.911134  22.888784
4 -109.910801  22.888351
5 -109.910768  22.888334
6 -109.910726  22.888322
7 -109.910695  22.888319
8 -109.910669  22.888323
9 -109.910641  22.888332

##  Use the GeoViews `Path` function to configure a line plot by using `route_df`. Set a custom color and width for the line that may contrast with the map

In [30]:
# Configure the route path by using the GeoViews' Path function
route_path = gv.Path(route_df).opts(color="red",line_width=3)

In [31]:
# Display a composed plot by using the route_map and route_path objects
waypoints_map*route_path

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City)
   .Path.I   :Path   [Latitude,Longitude]